In [ ]:
!pip install transformers datasets accelerate peft


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.7/320.7 kB 21.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.4 MB/s eta 0:00:00


In [ ]:
import re

# Path to your Bible text file
input_file_path = "/content/cleaned_bible.txt"

# Read the content from the file
with open(input_file_path, 'r') as f:
    bible_text = f.read()

# Clean the text: remove numbers and non-alphabetic characters
cleaned_text = re.sub(r'[^a-zA-Z\s]', '', bible_text)

# Save the cleaned text to a new file
output_file_path = 'cleaned_corpse.txt'
with open(output_file_path, 'w') as f:
    f.write(cleaned_text)

print(f"Cleaned text saved to {output_file_path}")


Cleaned text saved to cleaned_corpse.txt


In [ ]:
import os

# Check if the file exists
file_path = '/content/cleaned_corpse (1).txt'
print(os.path.exists(file_path))  # This should return True if the file exists


True


In [ ]:
from datasets import load_dataset

# Load the cleaned dataset using the correct path
dataset = load_dataset('text', data_files='/content/cleaned_corpse (1).txt', split='train')


Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

model_name = "facebook/llama-7b"  # Replace with your model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)


OSError: facebook/llama-7b is not a local folder and is not a valid model identifier listed on 'https://huggingface.co/models'
If this is a private repository, make sure to pass a token having permission to this repo either by logging in with `huggingface-cli login` or by passing `token=<your_token>`

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

# Replace with a publicly available model
model_name = "gpt2"  # Example of a publicly available model

# Load the model and tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [ ]:
from peft import LoraConfig, get_peft_model

# Set LoRA configuration
lora_config = LoraConfig(
    r=8,  # Rank
    lora_alpha=32,
    lora_dropout=0.1,
    bias="none",
)

# Get the PEFT model
lora_model = get_peft_model(model, lora_config)


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1150: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(


In [ ]:
def tokenize_function(examples):
    return tokenizer(examples['text'], truncation=True, padding="max_length", max_length=512)

tokenized_dataset = dataset.map(tokenize_function, batched=True)


Map:   0%|          | 0/1 [00:00<?, ? examples/s]

ValueError: Asking to pad but the tokenizer does not have a padding token. Please select a token to use as `pad_token` `(tokenizer.pad_token = tokenizer.eos_token e.g.)` or add a new pad token via `tokenizer.add_special_tokens({'pad_token': '[PAD]'})`.

In [ ]:
from datasets import load_dataset
from transformers import AutoTokenizer

# Load your dataset
dataset = load_dataset('text', data_files='/content/cleaned_corpse (1).txt', split='train')

# Load the tokenizer
model_name = "gpt2"  # Replace with your specific model
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Set pad token
tokenizer.pad_token = tokenizer.eos_token  # or use tokenizer.add_special_tokens({'pad_token': '[PAD]'})

# Tokenization function
def tokenize_function(examples):
    return tokenizer(examples['text'], truncation=True, padding="max_length", max_length=512)

# Tokenize the dataset
tokenized_dataset = dataset.map(tokenize_function, batched=True)


Map:   0%|          | 0/1 [00:00<?, ? examples/s]

In [ ]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir="./lora_model",
    evaluation_strategy="epoch",
    learning_rate=5e-5,
    per_device_train_batch_size=4,
    num_train_epochs=3,
    save_strategy="epoch",
)


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
5fbe32ae3285a6f6f556f19d606c691c1855aba6

In [ ]:
trainer = Trainer(
    model=lora_model,
    args=training_args,
    train_dataset=tokenized_dataset,
)

# Train the model
trainer.train()


wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


ValueError: The model did not return a loss from the inputs, only the following keys: logits,past_key_values. For reference, the inputs it received are input_ids,attention_mask.

In [ ]:
def tokenize_function(examples):
    return tokenizer(
        examples['text'],
        truncation=True,
        padding="max_length",
        max_length=512,
        return_tensors='pt'
    )

# Include labels for the model
def tokenize_function_with_labels(examples):
    tokenized = tokenizer(
        examples['text'],
        truncation=True,
        padding="max_length",
        max_length=512
    )
    tokenized["labels"] = tokenized["input_ids"].copy()  # Set labels to be the same as input_ids
    return tokenized

tokenized_dataset = dataset.map(tokenize_function_with_labels, batched=True)


Map:   0%|          | 0/1 [00:00<?, ? examples/s]

In [ ]:
from transformers import Trainer, TrainingArguments, AutoModelForCausalLM

# Load your model
model_name = "gpt2"  # Replace with your specific model
model = AutoModelForCausalLM.from_pretrained(model_name)

# Define training arguments
training_args = TrainingArguments(
    output_dir="./lora_model",
    per_device_train_batch_size=2,
    num_train_epochs=400,
    logging_dir='./logs',
    logging_steps=10,
    report_to='wandb',
    run_name='my_run'  # Specify a unique run name
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset,
)

# Train the model
trainer.train()


wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


TrainOutput(global_step=400, training_loss=0.2581819037068635, metrics={'train_runtime': 4115.0071, 'train_samples_per_second': 0.097, 'train_steps_per_second': 0.097, 'total_flos': 104516812800000.0, 'train_loss': 0.2581819037068635, 'epoch': 400.0})

In [ ]:
trainer.save_model("./lora_model")  # Save the model to the specified directory


In [ ]:
import os

model_dir = './lora_model'  # Change to your model directory
print("Files in model directory:")
print(os.listdir(model_dir))


Files in model directory:
['generation_config.json', 'model.safetensors', 'checkpoint-400', 'training_args.bin', 'config.json']


In [ ]:
# After training your model
model.save_pretrained("./lora_model")
tokenizer.save_pretrained("./lora_model")


('./lora_model/tokenizer_config.json',
 './lora_model/special_tokens_map.json',
 './lora_model/vocab.json',
 './lora_model/merges.txt',
 './lora_model/added_tokens.json',
 './lora_model/tokenizer.json')

In [ ]:
from transformers import GPT2Tokenizer, AutoModelForCausalLM

model_name = "./lora_model"

# Load the specific tokenizer and model
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "bonse kutemwani ninshi  "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=100, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
bonse kutemwani ninshi    Moneni ndepanga imyulu iipya ne sonde ilipya Kabili ifya kale mukafilaba Kabili tafyakese na mu mutima wenu Esaya   moneni na  Petro  nwtCW     WATCH TOWER BIBLE AND TRACT SOCIETY OF PENNSYLVANIA  Watchtower Drive Patterson NY  USA AB


In [ ]:
pip install pyttsx3


In [ ]:
!sudo apt-get install espeak


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  espeak-data libespeak1 libportaudio2 libsonic0
The following NEW packages will be installed:
  espeak espeak-data libespeak1 libportaudio2 libsonic0
0 upgraded, 5 newly installed, 0 to remove and 49 not upgraded.
Need to get 1,382 kB of archives.
After this operation, 3,178 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libportaudio2 amd64 19.6.0-1.1 [65.3 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/main amd64 libsonic0 amd64 0.2.0-11build1 [10.3 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy/universe amd64 espeak-data amd64 1.48.15+dfsg-3 [1,085 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libespeak1 amd64 1.48.15+dfsg-3 [156 kB]
Get:5 http://archive.ubuntu.com/ubuntu jammy/universe amd64 espeak amd64 1.48.15+dfsg-3 [64.2 kB]
Fetched 1,382 kB in 0s (10.2 M

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import pyttsx3

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "ukutendeka lesa ali pangile isonde "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)

# Convert generated text to speech using pyttsx3
engine = pyttsx3.init()
engine.say(generated_text)  # Speak the generated text
engine.runAndWait()  # Wait for the speaking to finish


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
ukutendeka lesa ali pangile isonde      Moneni ndepanga imyulu iipya na    Moneni na  ndepanga imyulu iipya na   Moneni


In [ ]:
!pip install gTTS


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
from gtts import gTTS
import os

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "ukutendeka lesa ali pangile isonde "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)

# Convert generated text to speech using gTTS
tts = gTTS(text=generated_text, lang='en')  # Change 'en' to the desired language code if needed
tts.save("output.mp3")  # Save the audio file

# Play the audio file
os.system("start output.mp3")  # On macOS, use "open"; on Linux, use "xdg-open"


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
ukutendeka lesa ali pangile isonde      Moneni ndepanga imyulu iipya na    Moneni na  ndepanga imyulu iipya na   Moneni


32512

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
from gtts import gTTS
from IPython.display import Audio, display

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "adam alilya ichisabo "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)

# Convert generated text to speech using gTTS
tts = gTTS(text=generated_text, lang='en')  # Change 'en' to the desired language code if needed
tts.save("output.mp3")  # Save the audio file

# Play the audio in Google Colab
display(Audio("output.mp3", autoplay=True))


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
adam alilya ichisabo      Moneni ndepanga imyulu iipya ne sonde ilipya ne sonde ilipya ne sonde ilipya ne sonde ilipya ne


In [ ]:
from transformers import RobertaTokenizer, RobertaForMaskedLM

# Load pre-trained RoBERTa tokenizer and model
model_name = "roberta-base"  # Open-source RoBERTa model
tokenizer = RobertaTokenizer.from_pretrained(model_name)
model = RobertaForMaskedLM.from_pretrained(model_name)

# Input sentence with a masked word
input_text = "Lesa alipanaga <mask> isonde"

# Tokenize the input and convert to tensor
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Run the model to predict the masked token
with torch.no_grad():
    output = model(input_ids)

# Get the top 5 token predictions for the <mask> token
mask_token_index = torch.where(input_ids == tokenizer.mask_token_id)[1]
mask_token_logits = output.logits[0, mask_token_index, :]
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()

# Decode the predicted tokens
predicted_words = [tokenizer.decode([token]) for token in top_5_tokens]

print("Predicted words for the masked token:", predicted_words)


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/481 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

Predicted words for the masked token: [',', ' en', ' de', ' la', ' et']


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model
model_name = "./lora_model"  # Path to the fine-tuned model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = " Shikulu mwandi atishani  "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text with temperature and top_p for more varied outputs
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(
        input_ids,
        max_length=100,
        num_return_sequences=1,
        temperature=0.7,  # Add more randomness
        top_p=0.9,        # Use nucleus sampling
        top_k=50          # Use top-k sampling
    )

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:567: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.7` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:572: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
 Shikulu mwandi atishani    Moneni ndepanga imyulu iipya ne sonde ilipya Kabili ifya kale mukafilaba Kabili tafyakese na mu mutima wenu Esaya   moneni na  Petro  nwtCW     WATCH TOWER BIBLE AND TRACT SOCIETY OF PENNSYLVANIA  Watchtower Drive Patterson NY  USA ABAS


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Path to your fine-tuned model directory
model_name = "./lora_model"

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the pad token
tokenizer.pad_token_id = tokenizer.eos_token_id

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "bonse kutemwa ninshi"
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Create attention mask
attention_mask = torch.ones(input_ids.shape, dtype=torch.long)

# Generate text with sampling and temperature control
with torch.no_grad():
    output = model.generate(
        input_ids,
        attention_mask=attention_mask,
        max_length=50,
        num_return_sequences=1,
        do_sample=True,             # Enable sampling
        top_k=50,                   # Use top-k sampling
        top_p=0.95,                 # Nucleus sampling
        temperature=0.3,            # Control diversity
        pad_token_id=tokenizer.eos_token_id
    )

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


Generated Text:
bonse kutemwa ninshi mu ciNgeleshi iya New World Translation of the Holy Scriptures iyo bapitulukamo iya mu  Shikulu Mulopwe Yehova  YHWH


In [ ]:
!pip install streamlit
!pip install pyngrok
!pip install transformers torch


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.9/41.9 kB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.7/8.7 MB 23.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 40.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.3/79.3 kB 5.0 MB/s eta 0:00:00


In [ ]:
%%writefile app.py
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import streamlit as st

# Load the model and tokenizer
model_name = "./lora_model"  # Path to your model

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set model to evaluation mode
model.eval()

# Streamlit app title
st.title("Text Generation with Fine-tuned Model")

# Input text prompt from user
input_text = st.text_area("Enter your text prompt:", "Shikulu mwandi atishani")

# Button to generate text
if st.button("Generate"):
    # Encode the input text
    input_ids = tokenizer.encode(input_text, return_tensors='pt')

    # Generate text with temperature and sampling control
    with torch.no_grad():
        output = model.generate(
            input_ids,
            max_length=50,
            num_return_sequences=1,
            do_sample=True,
            top_k=50,
            top_p=0.95,
            temperature=0.7,
            pad_token_id=tokenizer.eos_token_id
        )

    # Decode the generated text
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

    # Display the generated text
    st.write("Generated Text:")
    st.write(generated_text)


Writing app.py


In [ ]:
!npm install -g localtunnel



added 22 packages, and audited 23 packages in 3s

3 packages are looking for funding
  run `npm fund` for details

1 moderate severity vulnerability

To address all issues (including breaking changes), run:
  npm audit fix --force

Run `npm audit` for details.


In [ ]:
! pip install streamlit -q

In [ ]:
!wget -q -O - ipv4.icanhazip.com


34.29.104.162


In [ ]:
!apt-get install nodejs
!apt-get install npm
!npm install -g localtunnel


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  javascript-common libc-ares2 libjs-highlight.js libnode72 nodejs-doc
Suggested packages:
  apache2 | lighttpd | httpd npm
The following NEW packages will be installed:
  javascript-common libc-ares2 libjs-highlight.js libnode72 nodejs nodejs-doc
0 upgraded, 6 newly installed, 0 to remove and 49 not upgraded.
Need to get 13.7 MB of archives.
After this operation, 54.0 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/main amd64 javascript-common all 11+nmu1 [5,936 B]
Get:2 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libjs-highlight.js all 9.18.5+dfsg1-1 [367 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 libc-ares2 amd64 1.18.1-1ubuntu0.22.04.3 [45.1 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 libnode72 amd64 12.22.9~dfsg-1ubuntu3.6 [10.8 MB]


In [ ]:
!npm install -g localtunnel


changed 22 packages, and audited 23 packages in 2s

3 packages are looking for funding
  run `npm fund` for details

1 moderate severity vulnerability

To address all issues (including breaking changes), run:
  npm audit fix --force

Run `npm audit` for details.


In [ ]:
!apt-get install npm

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
npm is already the newest version (8.5.1~ds-1).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.


In [ ]:
!streamlit run app.py & !npx localtunnel --port 8501


/bin/bash: line 1: !npx: command not found



  You can now view your Streamlit app in your browser.

  Local URL: http://localhost:8501
  Network URL: http://172.28.0.12:8501
  External URL: http://34.29.104.162:8501

  Stopping...


In [ ]:
!pip install gradio


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.6/50.6 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.7/56.7 MB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 319.8/319.8 kB 18.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.6/94.6 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.0/78.0 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 447.4/447.4 kB 17.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 144.5/144.5 kB 10.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.9/10.9 MB 25.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 1.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.7/63.7 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.2/13

In [ ]:
import gradio as gr
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Path to your fine-tuned model directory
model_name = "./lora_model"

# Load your model and tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the pad token
tokenizer.pad_token_id = tokenizer.eos_token_id

# Function to generate text
def generate_text(input_text):
    input_ids = tokenizer.encode(input_text, return_tensors="pt")

    # Create attention mask
    attention_mask = torch.ones(input_ids.shape, dtype=torch.long)

    # Generate text with sampling and temperature control
    with torch.no_grad():
        output = model.generate(
            input_ids,
            attention_mask=attention_mask,
            max_length=100,
            num_return_sequences=2,
            do_sample=True,             # Enable sampling
            top_k=40,                   # Use top-k sampling
            top_p=0.90,                 # Nucleus sampling
            temperature=0.8,            # Control diversity
            pad_token_id=tokenizer.eos_token_id
        )

    # Decode the output
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
    return generated_text

# Define Gradio interface
iface = gr.Interface(
    fn=generate_text,
    inputs="text",
    outputs="text",
    title="Text Generation with Your Model",
    description="Input a sentence to generate text using the fine-tuned model.",
    theme="default"
)

# Launch the Gradio app
iface.launch()


Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://3953252a9fceecacd7.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load your fine-tuned Bemba language model
model_name = "./lora_model"  # Replace with your model path or identifier
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the pad token
tokenizer.pad_token_id = tokenizer.eos_token_id

# Set the model to evaluation mode
model.eval()

# Prepare your input text in Bemba
input_text = " Noa na bana bakwe abaume kabili abebele"
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Create attention mask
attention_mask = torch.ones(input_ids.shape, dtype=torch.long)

# Generate text with sampling and temperature control
with torch.no_grad():
    output = model.generate(
        input_ids,
        attention_mask=attention_mask,
        max_length=100,
        num_return_sequences=1,
        do_sample=True,             # Enable sampling
        top_k=50,                   # Use top-k sampling
        top_p=0.95,                 # Nucleus sampling
        temperature=0.7,            # Control diversity
        pad_token_id=tokenizer.eos_token_id
    )

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


Generated Text:
 Noa na bana bakwe abaume kabili abebele na mu ciNgeleshi iya New World Translation of the Holy Scriptures iyo bapitulukamo iya mu  Shikulu Mulopwe Yehova  YHWH alanda ati     Moneni ndepanga imyulu iipya ne sonde ilipya Kabili ifya kale mukafilaba Kabili tafy


Fine tunnig model even further

In [ ]:
# Load the corpus from a text file
with open('bemba_corpse.txt', 'r', encoding='utf-8') as file:
    corpus = file.read()

# Split the corpus into sentences
sentences = corpus.split('\n')

# Clean up the sentences
sentences = [sentence.strip() for sentence in sentences if sentence.strip()]

# Save the sentences to a new file
output_file_path = 'sentences.txt'  # Specify the output file path
with open(output_file_path, 'w', encoding='utf-8') as output_file:
    for sentence in sentences:
        output_file.write(sentence + '\n')

print(f"Sentences saved to {output_file_path}")



Sentences saved to sentences.txt


In [ ]:
# Load the sentences from the file into a dataset
dataset = load_dataset('text', data_files={'train': 'sentences.txt'})

# Check the number of samples in the dataset
print(f"Number of samples in the dataset: {len(dataset['train'])}")

# If the dataset has more than 1 sample, proceed with tokenization and splitting
if len(dataset['train']) > 1:
    # Tokenize the dataset
    tokenized_dataset = dataset['train'].map(tokenize_function, batched=True)

    # Split the dataset into training and evaluation sets
    train_test_split = tokenized_dataset.train_test_split(test_size=0.1)  # 10% for evaluation
    train_dataset = train_test_split['train']
    eval_dataset = train_test_split['test']

    # Prepare the trainer
    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=eval_dataset,  # Add evaluation dataset here
    )

    # Start training
    trainer.train()
else:
    print("Dataset is too small to split. Please add more samples.")


Number of samples in the dataset: 1
Dataset is too small to split. Please add more samples.


In [ ]:
# Check the number of samples again
print(f"Number of samples in the dataset: {len(dataset['train'])}")

if len(dataset['train']) > 1:
    # Proceed with tokenization and splitting as previously discussed
    tokenized_dataset = dataset['train'].map(tokenize_function, batched=True)
    train_test_split = tokenized_dataset.train_test_split(test_size=0.1)
    train_dataset = train_test_split['train']
    eval_dataset = train_test_split['test']

    # Prepare and start training
    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=eval_dataset,
    )

    trainer.train()


Number of samples in the dataset: 1


In [ ]:
# Read sentences from the file
with open('/content/sentences.txt', 'r', encoding='utf-8') as f:
    sentences = f.readlines()

# Clean up the sentences by stripping whitespace and newline characters
sentences = [s.strip() for s in sentences if s.strip()]  # Remove empty strings
print(f"Number of sentences: {len(sentences)}")
print(sentences)  # Display the sentences if needed


Number of sentences: 1
['Mu Baibo mwaba amabuuku ayalekanalekana  Aya amabuuku yaba mu fipande fibili icipande ca kubalilapo Malembo ya ciHebere ne ciAramaic Icipangano ca Kale e lyo icipande ca bubili Malembo ya ciGriki Icipangano Cipya Ibuuku limo na limo balilyakanya mu fipandwa ne fikomo Nga balemba ilembo inamba ya kubali lapo iikonkana ne shina lye buuku imininako icipandwa e lyo inamba nangu amana mba ayakonkelepo yemininako icikomo nelyo ifikomo Ku ca kumwenako nga bale mba ifi Ukutendeka  ninshi balepilibula ukuti Ukutendeka icipandwa  icikomo  Ifyaba mu Cebo ca kwa Lesa Muli Baibo mwaliba amashiwi ya kwa Lesa ayo afwaya ukuti twishibe muno nshiku Ilatusambilisha ifyo twingacita pa kuti ifintu filetuwamina mu mikalile yesu e lyo ne fyo twingacita pa kuti Lesa atutemwe Ilasuka na mepusho yakonkapo   Bushe Lesa nani   Kuti mwacita shani pa kuti musambilile pali Lesa   Nani umwine wa Baibo   Bushe ifyo Baibo yalanda pa fya sayansi fya cine   Finshi ifyaba mu Baibo   Finshi Baibo 

In [ ]:
# Save the sentences back to a text file if needed (optional)
with open('bemba_sentences.txt', 'w', encoding='utf-8') as f:
    for sentence in sentences:
        f.write(sentence + '\n')  # Write each sentence on a new line


In [ ]:
from datasets import load_dataset

# Load the dataset from sentence.txt
dataset = load_dataset('text', data_files={'train': 'bemba_sentences.txt'})
print(dataset)


Generating train split: 0 examples [00:00, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 1
    })
})


In [ ]:
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForCausalLM, Trainer, TrainingArguments

# Load the tokenizer and model
model_name = "./lora_model"  # Replace with your model name or path
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Load the sentences from the file into a dataset
dataset = load_dataset('text', data_files={'train': 'sentences.txt'})

# Tokenize the dataset
def tokenize_function(examples):
    tokenized_inputs = tokenizer(examples['text'], padding='max_length', truncation=True)
    tokenized_inputs['labels'] = tokenized_inputs['input_ids']  # Set labels to input_ids for training
    return tokenized_inputs

# Tokenize the dataset
tokenized_dataset = dataset['train'].map(tokenize_function, batched=True)

# Check the number of samples
num_samples = len(tokenized_dataset)

if num_samples > 1:
    # Split the dataset into training and evaluation sets
    train_test_split = tokenized_dataset.train_test_split(test_size=0.1)  # 10% for evaluation
    train_dataset = train_test_split['train']
    eval_dataset = train_test_split['test']
else:
    # Use the same dataset for training and evaluation if it's too small
    train_dataset = tokenized_dataset
    eval_dataset = tokenized_dataset  # Use the same dataset for evaluation

# Prepare the trainer
training_args = TrainingArguments(
    output_dir='./results',
    evaluation_strategy='epoch',  # Change to eval_strategy if you're using a future version
    learning_rate=5e-5,
    per_device_train_batch_size=1,  # Use a batch size of 1
    num_train_epochs=20,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,  # Add evaluation dataset here
)

# Start training
trainer.train()


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


TrainOutput(global_step=20, training_loss=4.529143142700195, metrics={'train_runtime': 571.3813, 'train_samples_per_second': 0.035, 'train_steps_per_second': 0.035, 'total_flos': 10451681280000.0, 'train_loss': 4.529143142700195, 'epoch': 20.0})

In [ ]:
# After trainer.train()
trainer.save_model('./results')  # Save the model to the specified directory
tokenizer.save_pretrained('./results')  # Save the tokenizer


('./results/tokenizer_config.json',
 './results/special_tokens_map.json',
 './results/vocab.json',
 './results/merges.txt',
 './results/added_tokens.json',
 './results/tokenizer.json')

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model (make sure to specify the correct path to your model)
model_name = "./results"  # Change this to where your model is saved
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

def generate_text(prompt, max_length=100, temperature=0.9, top_k=50, top_p=0.9):
    # Encode the input prompt
    input_ids = tokenizer.encode(prompt, return_tensors='pt')

    # Generate text
    with torch.no_grad():
        outputs = model.generate(
            input_ids,
            max_length=max_length,
            num_return_sequences=2,
            temperature=temperature,
            top_k=top_k,
            top_p=top_p,
            do_sample=True  # Enable sampling
        )

    # Decode the generated text
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return generated_text

# Test the model with a prompt
test_prompt = "Lyena Lesa atile Te cisuma umuntu aleikala fye eka Nalamupangila uwa kuti alemwafwa  "
generated_output = generate_text(test_prompt)

print("Generated Output:")
print(generated_output)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Output:
Lyena Lesa atile Te cisuma umuntu aleikala fye eka Nalamupangila uwa kuti alemwafwa    Moneta atile Te cisuma umuntu lyonaba   Moneta atile Te cisuma umuntu lyonaba    moneta atile namo illea   moneta atile lwe na  moneta atile    moneta atile ci   moneta


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model (make sure to specify the correct path to your model)
model_name = "./results"  # Change this to where your model is saved
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

def generate_text(prompt, max_length=50, temperature=0.8, top_k=50, top_p=0.8):
    # Encode the input prompt
    input_ids = tokenizer.encode(prompt, return_tensors='pt')

    # Create attention mask
    attention_mask = torch.ones(input_ids.shape, dtype=torch.long)

    # Generate text
    with torch.no_grad():
        outputs = model.generate(
            input_ids,
            attention_mask=attention_mask,  # Pass the attention mask
            max_length=max_length,
            num_return_sequences=1,
            temperature=temperature,
            top_k=top_k,
            top_p=top_p,
            do_sample=True,  # Enable sampling
            pad_token_id=tokenizer.eos_token_id  # Specify the padding token ID
        )

    # Decode the generated text
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return generated_text

# Test the model with a prompt
test_prompt = "kutemwa ninshi "
generated_output = generate_text(test_prompt)

print("Generated Output:")
print(generated_output)


Generated Output:
kutemwa ninshi bhi wani yonse kutemwa mu ci sonde mwanga iwa ya kutemwa mu ci sonde mwanga iwa ya kutemwa mu ci


In [ ]:
# Load the dataset from your text file
dataset = load_dataset('text', data_files={'train': 'bemba_corpse.txt'})

# Check the number of samples in your dataset
print("Number of samples in the dataset:", len(dataset['train']))


Number of samples in the dataset: 1


In [ ]:
if len(dataset['train']) > 1:
    train_test_split = dataset['train'].train_test_split(test_size=0.1)  # 10% for evaluation
    train_dataset = train_test_split['train']
    eval_dataset = train_test_split['test']
else:
    # Use the entire dataset for training
    train_dataset = dataset['train']
    eval_dataset = None  # or set to a minimal eval dataset


In [ ]:
# Set training arguments
training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch" if eval_dataset else "no",  # Set strategy based on eval dataset presence
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    num_train_epochs=3,
    weight_decay=0.01,
)

# Create the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,  # May be None
)

# Start training
trainer.train()


ValueError: The batch received was empty, your model won't be able to train on it. Double-check that your training dataset contains keys expected by the model: input_ids,past_key_values,attention_mask,token_type_ids,position_ids,head_mask,inputs_embeds,encoder_hidden_states,encoder_attention_mask,labels,use_cache,output_attentions,output_hidden_states,return_dict,label_ids,label,labels.

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM, Trainer, TrainingArguments
from datasets import load_dataset

# Load your fine-tuned Bemba language model
model_name = "./lora_model"  # Replace with your model path or identifier
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Load the dataset from your text file
dataset = load_dataset('text', data_files={'train': 'bemba_corpse.txt'})

# Split the dataset into training and evaluation sets
train_test_split = dataset['train'].train_test_split(test_size=0.1)  # 10% for evaluation
train_dataset = train_test_split['train']
eval_dataset = train_test_split['test']

# Define the tokenization function
def tokenize_function(examples):
    tokenized_inputs = tokenizer(examples['text'], padding="max_length", truncation=True, return_tensors='pt')
    tokenized_inputs['labels'] = tokenized_inputs['input_ids'].clone()
    tokenized_inputs['labels'][:, :-1] = tokenized_inputs['input_ids'][:, 1:]  # Shift left
    tokenized_inputs['labels'][:, -1] = -100  # Ignore the last token
    return tokenized_inputs

# Tokenize the datasets
tokenized_train_dataset = train_dataset.map(tokenize_function, batched=True)
tokenized_eval_dataset = eval_dataset.map(tokenize_function, batched=True)

# Set training arguments
training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",  # Change to "steps" if you want to evaluate more frequently
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    num_train_epochs=3,
    weight_decay=0.01,
)

# Create the Trainer with the evaluation dataset
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train_dataset,
    eval_dataset=tokenized_eval_dataset,  # Add the eval_dataset here
)

# Start training
trainer.train()


ValueError: With n_samples=1, test_size=0.1 and train_size=None, the resulting train set will be empty. Adjust any of the aforementioned parameters.

In [ ]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer

# Load a larger pretrained model
tokenizer = GPT2Tokenizer.from_pretrained("gpt2-large")  # Or any other large model
model = GPT2LMHeadModel.from_pretrained("gpt2-large")

# Continue with your text generation as before


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/666 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


model.safetensors:   0%|          | 0.00/3.25G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model
model_name = "./lora_model"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "Shikulu mwandi lesa."  # Provide a longer, more diverse prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text with repetition penalty
with torch.no_grad():
    output = model.generate(
        input_ids,
        max_length=50,
        num_return_sequences=1,
        temperature=0.2,
        top_p=0.9,
        top_k=50,
        repetition_penalty=1.5  # Penalize repetitive words
    )

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
Shikulu mwandi lesa.
Aya bapituluk na kwa  BHWH sarpindi. Mulopwe Yehova babombang iyaba yonse neeniputuli pa w


In [ ]:
import torch
from transformers import GPT2Tokenizer, GPT2LMHeadModel

# Load a larger pretrained model (GPT-2 Large)
model_name = "gpt2-large"  # Use GPT-2 Large for more capacity
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
model = GPT2LMHeadModel.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "Shikulu mwandi alikutendeka ati mukwete sana ichupo."  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text with repetition penalty and other strategies
with torch.no_grad():
    output = model.generate(
        input_ids,
        max_length=50,           # Maximum length of generated text
        num_return_sequences=1,   # Number of sequences to return
        temperature=0.7,          # Adjust temperature for diversity
        top_p=0.9,                # Nucleus sampling for generating more interesting output
        top_k=50,                 # Limits to the top-k predictions to control randomness
        repetition_penalty=1.5    # Penalizes word repetition
    )

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
Shikulu mwandi alikutendeka ati mukwete sana ichupo.

"I am a woman, and I have to be treated like one."


The man who was arrested for the


In [ ]:
from transformers import BertTokenizer, BertForMaskedLM
import torch

# Load pre-trained BERT tokenizer and model for Masked LM
model_name = "bert-base-uncased"  # Open-source BERT model
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertForMaskedLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Input sentence with a masked word
input_text = "Lesa alipanaga [MASK] isonde"  # The goal is for BERT to predict the masked word

# Tokenize the input and convert to tensor
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Get the index of the [MASK] token
mask_token_index = torch.where(input_ids == tokenizer.mask_token_id)[1]

# Run the model to predict the masked token
with torch.no_grad():
    output = model(input_ids)

# Extract the predictions for the masked token
mask_token_logits = output.logits[0, mask_token_index, :]

# Get the top 5 token predictions
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()

# Decode the predicted tokens
predicted_words = [tokenizer.decode([token]) for token in top_5_tokens]

print("Predicted words for the masked token:", predicted_words)


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Predicted words for the masked token: ['-', ',', '/', '##s', 'la']


In [ ]:
!pip install speechbrain

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 807.2/807.2 kB 27.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.8/117.8 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 722.2/722.2 kB 26.5 MB/s eta 0:00:00


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
from datasets import load_dataset
from IPython.display import Audio, display
from transformers import SpeechT5ForTextToSpeech, SpeechT5Processor
from speechbrain.pretrained import Tacotron2, HIFIGAN
import torchaudio

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model for text generation
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "ukutendeka lesa ali pangile isonde "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)

# Load Hugging Face SpeechBrain Tacotron2 model and HiFi-GAN vocoder for TTS
tacotron2 = Tacotron2.from_hparams(source="speechbrain/tts-tacotron2-ljspeech", savedir="tmpdir_tts")
hifi_gan = HIFIGAN.from_hparams(source="speechbrain/tts-hifigan-ljspeech", savedir="tmpdir_vocoder")

# Generate speech from the generated text
mel_output, mel_length, alignment = tacotron2.generate_spectrogram(generated_text)

# Convert spectrogram to waveform using HiFi-GAN vocoder
waveforms = hifi_gan.decode_batch(mel_output)

# Save the audio to an output file
torchaudio.save('output.wav', waveforms.squeeze(1), 22050)

# Play the audio in Google Colab
display(Audio('output.wav', autoplay=True))


<ipython-input-54-a9c94bb7bdc6>:6: UserWarning: Module 'speechbrain.pretrained' was deprecated, redirecting to 'speechbrain.inference'. Please update your script. This is a change from SpeechBrain 1.0. See: https://github.com/speechbrain/speechbrain/releases/tag/v1.0.0
  from speechbrain.pretrained import Tacotron2, HIFIGAN
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
ukutendeka lesa ali pangile isonde      Moneni ndepanga imyulu iipya na    Moneni na  ndepanga imyulu iipya na   Moneni


hyperparams.yaml:   0%|          | 0.00/2.20k [00:00<?, ?B/s]

model.ckpt:   0%|          | 0.00/113M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/speechbrain/utils/checkpoints.py:194: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(path, map_location=device

hyperparams.yaml:   0%|          | 0.00/1.16k [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


generator.ckpt:   0%|          | 0.00/55.8M [00:00<?, ?B/s]

AttributeError: 'Tacotron2' object has no attribute 'generate_spectrogram'

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
from datasets import load_dataset
from IPython.display import Audio, display
from transformers import SpeechT5ForTextToSpeech, SpeechT5Processor
from speechbrain.pretrained import Tacotron2, HIFIGAN
import torchaudio

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model for text generation
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "ukutendeka lesa ali pangile isonde "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)

# Load Hugging Face SpeechBrain Tacotron2 model and HiFi-GAN vocoder for TTS
tacotron2 = Tacotron2.from_hparams(source="speechbrain/tts-tacotron2-ljspeech", savedir="tmpdir_tts")
hifi_gan = HIFIGAN.from_hparams(source="speechbrain/tts-hifigan-ljspeech", savedir="tmpdir_vocoder")

# Generate mel-spectrogram from the generated text using Tacotron2's encode_text
mel_output, mel_length, _ = tacotron2.encode_text(generated_text)

# Convert spectrogram to waveform using HiFi-GAN vocoder
waveforms = hifi_gan.decode_batch(mel_output)

# Save the audio to an output file
torchaudio.save('output.wav', waveforms.squeeze(1), 22050)

# Play the audio in Google Colab
display(Audio('output.wav', autoplay=True))


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
ukutendeka lesa ali pangile isonde      Moneni ndepanga imyulu iipya na    Moneni na  ndepanga imyulu iipya na   Moneni


In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

# Path to your fine-tuned model directory
model_name = "./lora_model"  # Update if necessary

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "Lesa alipanaga isonde "  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Create an attention mask
attention_mask = torch.ones(input_ids.shape, dtype=torch.long)

# Set the pad token id
tokenizer.pad_token_id = tokenizer.eos_token_id  # Use the eos token as the pad token

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1, attention_mask=attention_mask)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generated Text:
Lesa alipanaga isonde était en la vie de la vie de la vie de la vie de la vie de la vie de la vie de la vie de la vie de la v


In [ ]:
import torch
from transformers import AutoTokenizer

# Load the tokenizer for your model
model_name = "./lora_model"  # Path to your fine-tuned model directory
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Example: Load your dataset from a text file
with open('/content/cleaned_corpse.txt', 'r', encoding='utf-8') as file:
    dataset = file.readlines()

# Tokenize and encode the dataset
encoded_dataset = []
for text in dataset:
    # Tokenize the text and convert to IDs
    encoded_text = tokenizer.encode(text, add_special_tokens=True, padding='max_length', truncation=True, max_length=512)
    encoded_dataset.append(encoded_text)

# Convert encoded data into tensors
tensor_dataset = torch.tensor(encoded_dataset)

# If you want to create attention masks
attention_masks = (tensor_dataset != tokenizer.pad_token_id).long()

# Print the shape of the tensor dataset and attention masks
print("Encoded Tensor Dataset Shape:", tensor_dataset.shape)
print("Attention Masks Shape:", attention_masks.shape)


Encoded Tensor Dataset Shape: torch.Size([1, 512])
Attention Masks Shape: torch.Size([1, 512])


In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM

# Load the tokenizer and model
model_name = "./lora_model"  # Path to your fine-tuned model directory
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

# Set the model to evaluation mode
model.eval()

# Prepare your input text
input_text = "In the beginning, God created"  # Replace with your test prompt
input_ids = tokenizer.encode(input_text, return_tensors='pt')

# Generate text
with torch.no_grad():  # Disable gradient calculation
    output = model.generate(input_ids, max_length=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print("Generated Text:")
print(generated_text)


OSError: Can't load tokenizer for './lora_model'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure './lora_model' is the correct path to a directory containing all relevant files for a GPT2TokenizerFast tokenizer.